In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

In [22]:
def read_files(path, filenames):
    """
    Reads all files and returns a dataframe with only the specificed columns
    """
    return pd.concat((pd.read_csv(path + f, skipinitialspace=True) for f in filenames))

def process_options(df_opt, call = True):
    """
    Cleans up column names and add time to live (Ttl) column to the dataframe
    """

    keys = {key: key[key.find("[")+1:key.find("]")][0] + key[key.find("[")+1:key.find("]")][1:].lower()  for key in df_opt.keys()}
    df_opt = df_opt.rename(columns=keys)

    if call:
        keys = {"C_ask": "Ask", "C_bid": "Bid"}
    else:
        keys = {"P_ask": "Ask", "P_bid": "Bid"}
    df_opt = df_opt.rename(columns=keys)

    df_opt["Quote_date"] = pd.to_datetime(df_opt["Quote_date"])
    df_opt["Expire_date"] = pd.to_datetime(df_opt["Expire_date"])
    df_opt["Ttl"] = df_opt.apply(lambda row: (row.Expire_date - row.Quote_date).days, axis = 1)

    columns = ["Quote_date", "Expire_date",  "Underlying_last", "Strike", "Ask", "Bid", "Ttl"]
    df_opt = df_opt[columns]
    df_opt = df_opt[df_opt["Ttl"] != 0]
    return df_opt[columns]

def process_rates(df_r):
    """
    Rename rate duration
    """
    df_r["Date"] = pd.to_datetime(df_r["Date"])
    df_r = df_r.rename(columns = {"Date" : "Quote_date", "3 Mo": "R"})
    #rate_keys = {key: key if key == "Date" else int(key.split(" ")[0])*30 if key.split(" ")[1] == "Mo" else int(key.split(" ")[0])*365  for key in df_r.keys()}
    #df_r = df_r.rename(columns=rate_keys)
    columns = ["Quote_date", "R"]
    return df_r[columns]

def combine_opt_r(df_opt, df_r):
    """
    Combines the dataset for options and rates
    """
    #df_opt["R"] = df_opt.apply(lambda row : df_rates[str(min(df_r.drop(["Date"], axis = 1).keys(), key = lambda x:abs(int(x)-row.Ttl)))][row.Quote_date], axis = 1)
    df_opt = pd.merge(df_opt, df_r, on ="Quote_date", how = "left")
    return df_opt

def get_model_dataset(path_opt, filenames_opt, path_r, filenames_r, call = True):
    """
    Wrapper function to extract option data and rates. Returns a combined dataframe
    """
    df_opt = read_files(path_opt, filenames_opt)
    df_r = read_files(path_r, filenames_r)
    df_opt = process_options(df_opt, call)
    df_r = process_rates(df_r)
    df = combine_opt_r(df_opt, df_r)
    return df.dropna() #TODO: Fix handling of nan values

In [33]:
path_opt = "C:/Users/Erlend/Google Drive/NTNU/5. Klasse/Prosjektoppgave/Data/option data/"
#filenames = ["spx_eod_" + str(year) + (str(month) if month >= 10 else "0"+str(month)) +".txt" for year in range(2010, 2022) for month in range(1, 13)] + ["spx_eod_2022" + (str(month) if month >= 10 else "0"+str(month)) +".txt" for month in range(1, 10)]
filenames_opt = ["spx_eod_202209.txt"]
path_r = "C:/Users/Erlend/Google Drive/NTNU/5. Klasse/Prosjektoppgave/Data/"
filenames_r = ["yield-curve-rates-2022.csv", "yield-curve-rates-1990-2021.csv"]

df = get_model_dataset(path_opt, filenames_opt, path_r, filenames_r, True)
print(df)
df.info()

       Quote_date Expire_date  Underlying_last   Strike     Ask     Bid   Ttl  \
0      2022-09-01  2022-09-02          3968.05   1000.0  2972.1  2961.6     1   
1      2022-09-01  2022-09-02          3968.05   1200.0  2771.9  2761.7     1   
2      2022-09-01  2022-09-02          3968.05   1400.0  2572.1  2561.7     1   
3      2022-09-01  2022-09-02          3968.05   1600.0  2368.2  2357.8     1   
4      2022-09-01  2022-09-02          3968.05   1800.0  2165.9  2158.1     1   
...           ...         ...              ...      ...     ...     ...   ...   
177070 2022-09-30  2026-12-18          3589.70   8800.0    31.4    10.0  1540   
177071 2022-09-30  2026-12-18          3589.70   9000.0    29.5     6.1  1540   
177072 2022-09-30  2026-12-18          3589.70   9200.0    16.2    11.2  1540   
177073 2022-09-30  2026-12-18          3589.70   9600.0    24.5     3.3  1540   
177074 2022-09-30  2026-12-18          3589.70  10000.0    21.8     7.3  1540   

           R  
0       2.97

In [35]:
def lstm_format(df, seq_length):
    """
    HIGHLY WIP
    Transforms a raw 2D list of option data into a 3D format of sequential data for LSTM model.
    """
    df["Option_key"] = df["Expire_date"].astype(str) + " | " + df["Strike"].astype(str)
    features = ["Underlying_last", "Strike", "Ttl", "R"]
    df["F"] = df[features].values.tolist()
    sequenses = []

    for option in df.Option_key.unique():
        df_opt = specific_option(df[df["Option_key" == option]], seq_length)




def specific_option(df, seq_length):
    """
    HIGHLY WIP
    Creates the sequential 3D format for a single option from a 2D list of all its quotes
    """
    for step in range(1,seq_length):
        df["F-"+str(step)] = df["F"].shift(step)
    df.info()
    return df


df = lstm_format(df, 5)
#print(df)
#df.info()

Here
  Quote_date Expire_date  Underlying_last  Strike     Ask     Bid  Ttl     R  \
0 2022-09-01  2022-09-02          3968.05  1000.0  2972.1  2961.6    1  2.97   

            Option_key                             F  F-1  F-2  F-3  F-4  
0  2022-09-02 | 1000.0  [3968.05, 1000.0, 1.0, 2.97]  NaN  NaN  NaN  NaN  
<class 'pandas.core.frame.DataFrame'>
Int64Index: 1 entries, 0 to 0
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Quote_date       1 non-null      datetime64[ns]
 1   Expire_date      1 non-null      datetime64[ns]
 2   Underlying_last  1 non-null      float64       
 3   Strike           1 non-null      float64       
 4   Ask              1 non-null      float64       
 5   Bid              1 non-null      float64       
 6   Ttl              1 non-null      int64         
 7   R                1 non-null      float64       
 8   Option_key       1 non-null      object        


<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stabl

Here
  Quote_date Expire_date  Underlying_last  Strike     Ask     Bid  Ttl     R  \
7 2022-09-01  2022-09-02          3968.05  2400.0  1568.4  1558.5    1  2.97   

            Option_key                             F  F-1  F-2  F-3  F-4  
7  2022-09-02 | 2400.0  [3968.05, 2400.0, 1.0, 2.97]  NaN  NaN  NaN  NaN  
<class 'pandas.core.frame.DataFrame'>
Int64Index: 1 entries, 7 to 7
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Quote_date       1 non-null      datetime64[ns]
 1   Expire_date      1 non-null      datetime64[ns]
 2   Underlying_last  1 non-null      float64       
 3   Strike           1 non-null      float64       
 4   Ask              1 non-null      float64       
 5   Bid              1 non-null      float64       
 6   Ttl              1 non-null      int64         
 7   R                1 non-null      float64       
 8   Option_key       1 non-null      object        


<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stabl


   Quote_date Expire_date  Underlying_last  Strike    Ask    Bid  Ttl     R  \
16 2022-09-01  2022-09-02          3968.05  3100.0  869.4  864.3    1  2.97   

             Option_key                             F  F-1  F-2  F-3  F-4  
16  2022-09-02 | 3100.0  [3968.05, 3100.0, 1.0, 2.97]  NaN  NaN  NaN  NaN  
<class 'pandas.core.frame.DataFrame'>
Int64Index: 1 entries, 16 to 16
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Quote_date       1 non-null      datetime64[ns]
 1   Expire_date      1 non-null      datetime64[ns]
 2   Underlying_last  1 non-null      float64       
 3   Strike           1 non-null      float64       
 4   Ask              1 non-null      float64       
 5   Bid              1 non-null      float64       
 6   Ttl              1 non-null      int64         
 7   R                1 non-null      float64       
 8   Option_key       1 non-null      object        
 9

...

<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stabl


<class 'pandas.core.frame.DataFrame'>
Int64Index: 13 entries, 2099 to 101309
Data columns (total 14 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   Quote_date       13 non-null     datetime64[ns]
 1   Expire_date      13 non-null     datetime64[ns]
 2   Underlying_last  13 non-null     float64       
 3   Strike           13 non-null     float64       
 4   Ask              13 non-null     float64       
 5   Bid              13 non-null     float64       
 6   Ttl              13 non-null     int64         
 7   R                13 non-null     float64       
 8   Option_key       13 non-null     object        
 9   F                13 non-null     object        
 10  F-1              12 non-null     object        
 11  F-2              11 non-null     object        
 12  F-3              10 non-null     object        
 13  F-4              9 non-null      object        
dtypes: datetime64[ns](2), float64(5), in

<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df["F-"+str(step)] = df["F"].shift(step)
<ipython-input-35-56b0174fc0bd>:21: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stabl


       Quote_date Expire_date  Underlying_last  Strike     Ask     Bid  Ttl  \
2102   2022-09-01  2022-09-21          3968.05  3000.0   970.5   964.2   20   
9694   2022-09-02  2022-09-21          3925.29  3000.0   923.2   916.1   19   
25042  2022-09-06  2022-09-21          3910.16  3000.0   913.1   906.4   15   
32607  2022-09-07  2022-09-21          3980.02  3000.0   982.3   976.3   14   
40208  2022-09-08  2022-09-21          4005.86  3000.0  1006.0  1000.2   13   
47777  2022-09-09  2022-09-21          4067.62  3000.0  1071.2  1064.4   12   
55341  2022-09-12  2022-09-21          4110.92  3000.0  1114.9  1102.0    9   
62984  2022-09-13  2022-09-21          3932.69  3000.0   934.2   927.3    8   
70677  2022-09-14  2022-09-21          3946.87  3000.0   950.1   942.5    7   
78372  2022-09-15  2022-09-21          3901.27  3000.0   907.6   900.1    6   
85887  2022-09-16  2022-09-21          3873.28  3000.0   880.4   869.8    5   
93370  2022-09-19  2022-09-21          3899.98  300

KeyboardInterrupt: 